In [16]:
# libraries
import pandas as pd
import numpy as np
import nltk
nltk.download('punkt_tab')
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from nltk.stem.porter import PorterStemmer

[nltk_data] Downloading package punkt_tab to C:\Users\Keerthi
[nltk_data]     Vasan\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


In [17]:

music_file = pd.read_csv('spotify_data.csv') #  Importing DataSet 
print("Initial ROW & COLUMNS:",music_file.shape)
modified_file = music_file.drop(columns=['link']) #dropping unwanted column
print("Row & Column after modification:",modified_file.shape)
modified_file['text'] = modified_file['text'].str.lower().replace(r'^\w\s','').replace(r'\n,','', regex=True) #preprocessing

Initial ROW & COLUMNS: (57650, 4)
Row & Column after modification: (57650, 3)


In [19]:


# 1. Slice the dataframe to match the matrix size
modified_file = modified_file.iloc[0:5000]

# 2. Reset the index so it goes 0, 1, 2... 4999
modified_file = modified_file.reset_index(drop=True)

modified_file.head(10)



artist                   song  \
0   ABBA  Ahe's My Kind Of Girl   
1   ABBA       Andante, Andante   
2   ABBA         As Good As New   
3   ABBA                   Bang   
4   ABBA       Bang-A-Boomerang   
5   ABBA     Burning My Bridges   
6   ABBA              Cassandra   
7   ABBA             Chiquitita   
8   ABBA            Crazy World   
9   ABBA        Crying Over You   

                                                text  
0  look at her face, it's a wonderful face  \r\na...  
1  take it easy with me, please  \r\ntouch me gen...  
2  i'll never know why i had to go  \r\nwhy i had...  
3  making somebody happy is a question of give an...  
4  making somebody happy is a question of give an...  
5  well, you hoot and you holler and you make me ...  
6  down in the street they're all singing and sho...  
7  chiquitita, tell me what's wrong  \r\nyou're e...  
8  i was out with the morning sun  \r\ncouldn't s...  
9  i'm waitin' for you baby  \r\ni'm sitting all ...

In [25]:
# sample_with_1K = modified_file.sample(100)
# print(sample_with_1K.shape)

# print(sample_with_1K.head(4))


In [20]:
ps = PorterStemmer() #stemming removes the suffix from the word
  
def token(txt):   # tokenization breaks the sentences into single words
    token = nltk.word_tokenize(txt)
    a = [ps.stem(w) for w in token]
    print(a)
    return " ".join(a)
# sample_with_1K['text'].apply(lambda x: token(x))

In [23]:
modified_file['text'].apply(lambda x: token(x))

tfid = TfidfVectorizer(analyzer='word',stop_words='english')
matrix = tfid.fit_transform(modified_file['text'])
similar_data = cosine_similarity(matrix)
similar_data[7]



['look', 'at', 'her', 'face', ',', 'it', "'s", 'a', 'wonder', 'face', 'and', 'it', 'mean', 'someth', 'special', 'to', 'me', 'look', 'at', 'the', 'way', 'that', 'she', 'smile', 'when', 'she', 'see', 'me', 'how', 'lucki', 'can', 'one', 'fellow', 'be', '?', 'she', "'s", 'just', 'my', 'kind', 'of', 'girl', ',', 'she', 'make', 'me', 'feel', 'fine', 'who', 'could', 'ever', 'believ', 'that', 'she', 'could', 'be', 'mine', '?', 'she', "'s", 'just', 'my', 'kind', 'of', 'girl', ',', 'without', 'her', 'i', "'m", 'blue', 'and', 'if', 'she', 'ever', 'leav', 'me', 'what', 'could', 'i', 'do', ',', 'what', 'could', 'i', 'do', '?', 'and', 'when', 'we', 'go', 'for', 'a', 'walk', 'in', 'the', 'park', 'and', 'she', 'hold', 'me', 'and', 'squeez', 'my', 'hand', 'we', "'ll", 'go', 'on', 'walk', 'for', 'hour', 'and', 'talk', 'about', 'all', 'the', 'thing', 'that', 'we', 'plan', 'she', "'s", 'just', 'my', 'kind', 'of', 'girl', ',', 'she', 'make', 'me', 'feel', 'fine', 'who', 'could', 'ever', 'believ', 'that', '

array([0.00396902, 0.0512871 , 0.03157851, ..., 0.0024115 , 0.00571258,
       0.01575174])

In [28]:
music_file[music_file['song'] == 'Butterfly Wings'].index[0]

47169

In [39]:
# recommendation function

def recommend(song_name):
    idx = music_file[music_file['song'] == song_name].index[0]
    distance = sorted(list(enumerate(similar_data[idx])), reverse=True, key= lambda x:x[1])
    song= []
    for s_id in distance[1:7] :
        song.append(music_file.iloc[s_id[0]].song)
    return song    
    

In [40]:
recommend("Burning My Bridges")

['Burning Up',
 'Do It',
 "I Won't Cry For You",
 'Gonna Sing You My Lovesong',
 'Tangled And Dark',
 "Tearin' It Up"]